コンペ終了後の実験
 LSTM CNN transformer 

## Get env

In [1]:
#!nvidia-smi

In [2]:
# 環境によって処理を変えるためのもの
import sys
import os
IN_COLAB = 'google.colab' in sys.modules
IN_KAGGLE = 'kaggle_web_client' in sys.modules
LOCAL = not (IN_KAGGLE or IN_COLAB)
print(f'IN_COLAB:{IN_COLAB}, IN_KAGGLE:{IN_KAGGLE}, LOCAL:{LOCAL}')

IN_COLAB:False, IN_KAGGLE:False, LOCAL:True


In [3]:
# For Colab Download some datasets
# ================================
if IN_COLAB:
    # mount googledrive
    from google.colab import drive
    drive.mount('/content/drive')
    # copy kaggle.json from googledrive
    ! pip install --upgrade --force-reinstall --no-deps  kaggle > /dev/null
    ! mkdir ~/.kaggle
    ! cp "/content/drive/MyDrive/kaggle/kaggle.json" ~/.kaggle/
    ! chmod 600 ~/.kaggle/kaggle.json
    
    if not os.path.exists("/content/input/"):
        !mkdir input
        !mkdir input/features
        !kaggle datasets download -d teyosan1229/ventilator-pressure
        !unzip /content/ventilator-pressure.zip -d input/features
        !kaggle competitions download -c ventilator-pressure-prediction
        !unzip /content/ventilator-pressure-prediction.zip -d input

In [4]:
if IN_KAGGLE or IN_COLAB:
    !pip install --upgrade -q wandb
    !pip install -q pytorch-lightning
    !pip install torch_optimizer==0.1.0
    !pip install einops

## Import Libraries

In [5]:
# Hide Warning
import warnings
warnings.filterwarnings('ignore', category=DeprecationWarning)
warnings.filterwarnings('ignore', category=FutureWarning)
warnings.filterwarnings('ignore', category=UserWarning)

# Python Libraries
import os
import math
import random
import glob
import pickle
import gc
from collections import defaultdict
from pathlib import Path

# Third party
import numpy as np
import pandas as pd
from tqdm.notebook import tqdm

# Visualizations
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
%matplotlib inline
sns.set(style="whitegrid")

# Utilities and Metrics
from sklearn.model_selection import StratifiedKFold, GroupKFold, KFold
from sklearn.preprocessing import RobustScaler, normalize, QuantileTransformer, StandardScaler
from sklearn.metrics import mean_absolute_error #[roc_auc_score, accuracy_score]

# Pytorch 
import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.optim import Adam, SGD
from torch.utils.data import Dataset, DataLoader, WeightedRandomSampler
from torch.optim.lr_scheduler import CosineAnnealingWarmRestarts, CosineAnnealingLR, ReduceLROnPlateau
from torch.optim.optimizer import Optimizer, required
import torch_optimizer as optim
from einops.layers.torch import Rearrange

# Pytorch Lightning
import pytorch_lightning as pl
from pytorch_lightning import Callback, seed_everything
from pytorch_lightning.callbacks import LearningRateMonitor, ModelCheckpoint, EarlyStopping
from pytorch_lightning.loggers import WandbLogger, CSVLogger

# Weights and Biases Tool
import wandb
os.environ["WANDB_API_KEY"]='68fa1bbcda0fcf7a56f3c33a0fafa45b02f1c52d'
wandb.login()

wandb: Currently logged in as: teyosan1229 (use `wandb login --relogin` to force relogin)


True

## Config

In [6]:
class CFG:
    debug = False
    competition='ventilator'
    exp_name = "ex04_2_reverseLSTM_821"
    seed = 29
    # model
    # img_size = 384
    
    # data
    target_col = 'pressure' # 目標値のある列名
    target_size = 1
    
    # optimizer
    optimizer_name = 'AdamW'#['RAdam']sgd AdamW
    lr = 2e-3 #3e-3,　2e-3
    weight_decay = 0.1
    amsgrad = False
    
    # scheduler
    epochs = 1024
#     scheduler = 'CosineAnnealingLR' #['CosineAnnealingLR', 'ReduceLROnPlateau']
#     T_max = 300
#     min_lr = 1e-5
    
    scheduler = 'ReduceLROnPlateau' #['CosineAnnealingLR', 'ReduceLROnPlateau']
    factor = 0.5
    patience = 10
    eps = 1e-6
    min_lr = 1e-05
    # criterion
    # u_out = 1 を考慮しないLoss
    criterion_name = 'CustomLoss1'
    
    # training
    train = True
    inference = True
    n_fold = 15
    trn_fold = [0,1,2,3,4,5,6,7,8,9,10,11,12,13,14]
    precision = 16 #[16, 32, 64]
    grad_acc = 1
    # DataLoader
    loader = {
        "train": {
            "batch_size": 512, # 512,
            "num_workers": 0,
            "shuffle": True,
            "pin_memory": True,
            "drop_last": True
        },
        "valid": {
            "batch_size": 1024,
            "num_workers": 0,
            "shuffle": False,
            "pin_memory": True,
            "drop_last": False
        }
    }
    # pl
    trainer = {
        'gpus': 1,
        'progress_bar_refresh_rate': 1,
        'benchmark': False,
        'deterministic': True,
        }

    # カテゴリ特徴量
    cate_cols = []
    # 連続値（スケーラー特徴用）
    cont_cols = []
    feature_cols = []
    
seed_everything(CFG.seed)
if not LOCAL:
    CFG.loader["train"]["num_workers"] = 4
    CFG.loader["valid"]["num_workers"] = 4

Global seed set to 29


In [7]:
len(CFG.feature_cols),CFG.loader["train"]["num_workers"]

(0, 0)

## Directory & LoadData

In [8]:
if IN_KAGGLE:
    INPUT_DIR = Path('../input/ventilator-pressure-prediction')
    FEAT_DIR = Path('../input/ventilator-pressure')
    OUTPUT_DIR = './'
elif IN_COLAB:
    INPUT_DIR = Path('/content/input/')
    FEAT_DIR = Path('/content/input/features/')
    OUTPUT_DIR = f'/content/drive/MyDrive/kaggle/Ventilator Pressure/{CFG.exp_name}/'
if LOCAL:
    INPUT_DIR = Path("F:/Kaggle/ventilator-pressure-prediction/data/input/")
    FEAT_DIR = Path("F:/Kaggle/ventilator-pressure-prediction/data/input/features/")
    OUTPUT_DIR = f'F:/Kaggle/ventilator-pressure-prediction/data/output/{CFG.exp_name}/'
    
df_train = pd.read_csv(INPUT_DIR / "train.csv")
df_test = pd.read_csv(INPUT_DIR / "test.csv")
#df_oof = df_train[["id","breath_id","u_out", "pressure", "fold"]].copy()

#CFG.cate_cols, CFG.cont_cols = get_cols_list(feats)
#CFG.feature_cols = CFG.cate_cols + CFG.cont_cols 

submission = pd.read_csv(INPUT_DIR / "sample_submission.csv")
display(df_train.head())
display(df_test.head())

if not os.path.exists(OUTPUT_DIR):
    os.makedirs(OUTPUT_DIR)

if CFG.debug:
    CFG.epochs = 5
    #CFG.inference = False
    df_train = df_train.head(80000)
    df_test = df_test.head(80000)

id  breath_id   R   C  time_step       u_in  u_out   pressure
0   1          1  20  50   0.000000   0.083334      0   5.837492
1   2          1  20  50   0.033652  18.383041      0   5.907794
2   3          1  20  50   0.067514  22.509278      0   7.876254
3   4          1  20  50   0.101542  22.808822      0  11.742872
4   5          1  20  50   0.135756  25.355850      0  12.234987

id  breath_id  R   C  time_step       u_in  u_out
0   1          0  5  20   0.000000   0.000000      0
1   2          0  5  20   0.031904   7.515046      0
2   3          0  5  20   0.063827  14.651675      0
3   4          0  5  20   0.095751  21.230610      0
4   5          0  5  20   0.127644  26.320956      0

In [9]:
def add_features(df): 
     
    df['sum_per_breath'] = df.groupby(['breath_id'])['u_in'].transform('sum') 
    
    # magic features start
    df['rounded_u_in'] = df['u_in'].round(0) 
    df['rank'] = df.groupby(['breath_id'])['time_step'].rank() 
    df['uid'] = df['R'].astype(str)+'_' + df['C'].astype(str) + '_' + df['rounded_u_in'].astype(str) + '_' + df['rank'].astype(str) 
    df['uid_count'] = df.groupby(['uid'])['uid'].transform('count') 
    df['f1'] = df.groupby(['uid'])['u_in'].transform('mean') 
    df['f2'] = df.groupby(['uid'])['u_in'].transform('min') 
    df['f3'] = df.groupby(['uid'])['u_in'].transform('max') 
    df['f4'] = df['u_in'] - df.groupby(['uid'])['u_in'].transform('mean') 
    df['f5'] = df['u_in'] - df.groupby(['uid'])['u_in'].transform('min') 
    df['f6'] = df['u_in'] - df.groupby(['uid'])['u_in'].transform('max') 
     
     
    del df['rounded_u_in'],df['rank'],df['uid'] 
    # magic features end
     
         
    df['u_in_diff_1'] = df.groupby(['breath_id'])['u_in'].diff(1) 
    df['u_in_diff_2'] = df.groupby(['breath_id'])['u_in'].diff(2) 
    df['u_in_diff_3'] = df.groupby(['breath_id'])['u_in'].diff(3) 
     
    df['u_in_diff_3'] = df['u_in_diff_3'].fillna(method='bfill') 
    df['u_in_diff_2'] = df['u_in_diff_2'].fillna(method='bfill') 
    df['u_in_diff_1'] = df['u_in_diff_1'].fillna(method='bfill') 
     
    df['time_step_diff_1'] = df.groupby(['breath_id'])['time_step'].diff(1).fillna(0) 
    df['time_step_diff_1_r'] = df.groupby(['breath_id'])['time_step'].diff(-1).fillna(0)  
    df['delta'] = df['time_step_diff_1'] * df['u_in'] 
    df['delta2'] = df['time_step_diff_1_r'] * df['u_in']  
    df['time_step_diff_2'] = df.groupby(['breath_id'])['time_step'].diff(2).fillna(0)  
    df['time_step_diff_3'] = df.groupby(['breath_id'])['time_step'].diff(3).fillna(0)  
 
    df['area'] = df.groupby(['breath_id'])['delta'].cumsum() 
    df['area2'] = df.groupby(['breath_id'])['delta2'].cumsum()  
    df['cross']= df['u_in']*df['u_out']  
    df['cross2']= df['time_step']*df['u_out']  
    df['u_in_cumsum'] = df.groupby(['breath_id'])['u_in'].cumsum() 
    df['area_cumsum'] = df.groupby(['breath_id'])['area'].cumsum()  
    df['max_to_cumsum_u_in_per_breath_id'] = df.groupby(['breath_id'])['u_in'].transform('max') - df['u_in_cumsum']  
     
    df['u_in_shift_1_past'] = df.groupby(['breath_id'])['u_in'].shift(1).fillna(0)  
    df['u_in_shift_2_past'] = df.groupby(['breath_id'])['u_in'].shift(2).fillna(0)  
    df['u_in_shift_3_past'] = df.groupby(['breath_id'])['u_in'].shift(3).fillna(0)  
     
    df['time_step_shift_1_past'] = df.groupby(['breath_id'])['time_step'].shift(1).fillna(0)  
    df['time_step_shift_2_past'] = df.groupby(['breath_id'])['time_step'].shift(2).fillna(0)  
    df['time_step_shift_3_past'] = df.groupby(['breath_id'])['time_step'].shift(3).fillna(0)  
 
    df['u_in_shift_1_future'] = df.groupby(['breath_id'])['u_in'].shift(-1).fillna(0)  
    df['u_in_shift_2_future'] = df.groupby(['breath_id'])['u_in'].shift(-2).fillna(0)  
    df['u_in_shift_3_future'] = df.groupby(['breath_id'])['u_in'].shift(-3).fillna(0) 
     
    df['time_step_shift_1_future'] = df.groupby(['breath_id'])['time_step'].shift(-1).fillna(0)  
    df['time_step_shift_2_future'] = df.groupby(['breath_id'])['time_step'].shift(-2).fillna(0)  
    df['time_step_shift_3_future'] = df.groupby(['breath_id'])['time_step'].shift(-3).fillna(0) 
     
    df['breath_id_u_out'] = df['breath_id'].astype(str) + '_' + df['u_out'].astype(str)  
    df['count_breath_id_u_out'] = df.groupby(['breath_id_u_out'])['breath_id_u_out'].transform('count')  
    del df['breath_id_u_out']  
 
    df['mean_u_in_per_R_C_u_out'] = df.groupby(['R','C','u_out'])['u_in'].transform('mean')  
    df['diff_mean_u_in_per_R_C_u_out'] = df['u_in'] - df['mean_u_in_per_R_C_u_out']  
    df['to_mean_u_in_per_R_C_u_out'] = df.groupby(['breath_id'])['u_in'].transform('mean') - df['mean_u_in_per_R_C_u_out']  
     
    df['max_u_in_per_R_C_u_out'] = df.groupby(['R','C','u_out'])['u_in'].transform('max')  
    df['diff_max_u_in_per_R_C_u_out'] = df['u_in'] - df['max_u_in_per_R_C_u_out']  
    df['to_max_u_in_per_R_C_u_out'] = df.groupby(['breath_id'])['u_in'].transform('max') - df['max_u_in_per_R_C_u_out'] 
 
    df['mean_u_out_per_breath_id'] = df.groupby(['breath_id'])['u_out'].transform('mean') 
     
     
    df['R_u_in'] = df['u_in'] * df['R']  
    df['C_u_in'] = df['u_in'] * df['C'] 
    df['u_out_shift_1_past'] = df.groupby(['breath_id'])['u_out'].shift(1).fillna(0)  
    df['u_out_shift_2_past'] = df.groupby(['breath_id'])['u_out'].shift(2).fillna(0)  
    df['u_out_shift_3_past'] = df.groupby(['breath_id'])['u_out'].shift(3).fillna(0) 
    df['u_out_shift_1_future'] = df.groupby(['breath_id'])['u_out'].shift(-1).fillna(0)  
    df['u_out_shift_2_future'] = df.groupby(['breath_id'])['u_out'].shift(-2).fillna(0)  
    df['u_out_shift_3_future'] = df.groupby(['breath_id'])['u_out'].shift(-3).fillna(0) 
    
    df['exponent']=(-1*df['time_step'])/(df['R']*df['C']) 
    df['factor']=np.exp(df['exponent']) 
    df['vf']=(df['u_in_cumsum']*df['R'])/df['factor'] 
    
    df['R'] = df['R'].astype(str)  
    df['C'] = df['C'].astype(str)  
    df['R_C'] = df['R'].astype(str) + '_' + df['C'].astype(str)  
    df = pd.get_dummies(df) 
 
    return df

def add_features2(df):
     
    df['rounded_u_in'] = df['u_in'].round(0) 
    df['rank'] = df.groupby(['breath_id'])['time_step'].rank() 
    df['uid'] = df['R'].astype(str)+'_' + df['C'].astype(str) + '_' + df['rounded_u_in'].astype(str) + '_' + df['rank'].astype(str) 
    df['uid_count'] = df.groupby(['uid'])['uid'].transform('count') 
    df['f1'] = df.groupby(['uid'])['u_in'].transform('mean') 
    df['f2'] = df.groupby(['uid'])['u_in'].transform('min') 
    df['f3'] = df.groupby(['uid'])['u_in'].transform('max') 
    df['f4'] = df['u_in'] - df.groupby(['uid'])['u_in'].transform('mean') 
    df['f5'] = df['u_in'] - df.groupby(['uid'])['u_in'].transform('min') 
    df['f6'] = df['u_in'] - df.groupby(['uid'])['u_in'].transform('max') 
     
     
    del df['rounded_u_in'],df['rank'],df['uid'] 
     
         
    df['u_in_diff_1'] = df.groupby(['breath_id'])['u_in'].diff(1)
    df['u_in_diff_2'] = df.groupby(['breath_id'])['u_in'].diff(2)

    df['u_in_diff_2'] = df['u_in_diff_2'].fillna(method='bfill')
    df['u_in_diff_1'] = df['u_in_diff_1'].fillna(method='bfill')
     
    df['time_step_diff_1'] = df.groupby(['breath_id'])['time_step'].diff(1).fillna(0) 
    df['delta'] = df['time_step_diff_1'] * df['u_in']
    
    del df['time_step_diff_1']
 
    df['area'] = df.groupby(['breath_id'])['delta'].cumsum()
    del df['delta']
    
    df['u_in_cumsum'] = df.groupby(['breath_id'])['u_in'].cumsum() 
    df['area_cumsum'] = df.groupby(['breath_id'])['area'].cumsum()  
     
    df['u_in_shift_1_past'] = df.groupby(['breath_id'])['u_in'].shift(1).fillna(0)  
    df['u_in_shift_2_past'] = df.groupby(['breath_id'])['u_in'].shift(2).fillna(0) 
 
    df['u_in_shift_1_future'] = df.groupby(['breath_id'])['u_in'].shift(-1).fillna(0)  
    df['u_in_shift_2_future'] = df.groupby(['breath_id'])['u_in'].shift(-2).fillna(0)   
     
    df['u_out_shift_1_past'] = df.groupby(['breath_id'])['u_out'].shift(1).fillna(0)  
    df['u_out_shift_2_past'] = df.groupby(['breath_id'])['u_out'].shift(2).fillna(0)
    df['u_out_shift_1_future'] = df.groupby(['breath_id'])['u_out'].shift(-1).fillna(0)
    
    del df['R'], df['C']
 
    return df

In [10]:
df_train.loc[df_train['u_out'] == 1, 'pressure'] = df_train['pressure'] * (-1)
df_train2 = df_train.copy()
df_test2 = df_test.copy()
# 並び替え
# ==============
df_train['rank'] = df_train.groupby(['breath_id'])['time_step'].rank()
df_train['neg_rank'] = -1 * df_train['rank']
df_test['rank'] = df_test.groupby(['breath_id'])['time_step'].rank()
df_test['neg_rank'] = -1 * df_test['rank']

df_train = df_train.sort_values(by=['breath_id','neg_rank']).reset_index(drop=True)
df_test = df_test.sort_values(by=['breath_id','neg_rank']).reset_index(drop=True)

del df_train['rank'],df_train['neg_rank'],df_test['rank'],df_test['neg_rank']
gc.collect()

df = pd.concat([df_train,df_test],axis=0,copy=False).reset_index(drop=True)
df = add_features(df)

train = df.iloc[:len(df_train),:]
test = df.iloc[len(df_train):,:].reset_index(drop=True)
print(train.shape, test.shape)
del test['pressure']
gc.collect()
# 正順特徴量
df2 = pd.concat([df_train2,df_test2],axis=0,copy=False).reset_index(drop=True)
df2 = add_features2(df2)

train2 = df2.iloc[:len(df_train2),:]
test2 = df2.iloc[len(df_train2):,:].reset_index(drop=True)
print(train2.shape, test2.shape)
del train2['pressure'], test2['pressure'], df2
gc.collect()

del train2['id'],train2['breath_id'],test2['id'],test2['breath_id']
gc.collect()

train2.columns = ['shifted_' + str(s) for s in train2.columns]
test2.columns = ['shifted_' + str(s) for s in test2.columns]

df_train = pd.concat([train,train2],axis=1,copy=False)
df_test = pd.concat([test,test2],axis=1,copy=False)

del train2, test2
gc.collect()

train

(6036000, 76) (4024000, 76)
(6036000, 25) (4024000, 25)


id  breath_id  time_step       u_in  u_out   pressure  \
0             80          1   2.689766   4.987079      1  -6.470211   
1             79          1   2.655746   4.984683      1  -6.540513   
2             78          1   2.621773   4.981847      1  -6.329607   
3             77          1   2.587754   4.978481      1  -6.610815   
4             76          1   2.553593   4.974474      1  -6.399909   
...          ...        ...        ...        ...    ...        ...   
6035995  6035925     125749   0.133124  16.101221      0  15.468886   
6035996  6035924     125749   0.099784  16.266744      0  15.117375   
6035997  6035923     125749   0.066365  21.614707      0   9.563505   
6035998  6035922     125749   0.033187  25.504196      0   5.345377   
6035999  6035921     125749   0.000000   6.030572      0   3.939334   

         sum_per_breath  uid_count         f1         f2  ...  C_50  \
0            811.680524      13686   4.985013   4.970322  ...     1   
1            811.680524      13686   4.982299   4.965039  ...     1   
2            811.680524      13686   4.979095   4.959016  ...     1   
3            811.680524      13686   4.975308   4.951984  ...     1   
4            811.680524      13686   4.970834   4.943761  ...     1   
...                 ...        ...        ...        ...  ...   ...   
6035995      392.912174        310  16.010447  15.501843  ...     0   
6035996      392.912174        192  16.025133  15.502960  ...     0   
6035997      392.912174        190  21.986672  21.503603  ...     0   
6035998      392.912174        163  25.952087  25.504196  ...     0   
6035999      392.912174        386   5.984519   5.500827  ...     0   

         R_C_20_10  R_C_20_20  R_C_20_50  R_C_50_10  R_C_50_20  R_C_50_50  \
0                0          0          1          0          0          0   
1                0          0          1          0          0          0   
2                0          0          1          0          0          0   
3                0          0          1          0          0          0   
4                0          0          1          0          0          0   
...            ...        ...        ...        ...        ...        ...   
6035995          0          0          0          1          0          0   
6035996          0          0          0          1          0          0   
6035997          0          0          0          1          0          0   
6035998          0          0          0          1          0          0   
6035999          0          0          0          1          0          0   

         R_C_5_10  R_C_5_20  R_C_5_50  
0               0         0         0  
1               0         0         0  
2               0         0         0  
3               0         0         0  
4               0         0         0  
...           ...       ...       ...  
6035995         0         0         0  
6035996         0         0         0  
6035997         0         0         0  
6035998         0         0         0  
6035999         0         0         0  

[6036000 rows x 76 columns]

In [11]:
print(len(df_train.columns.to_list()))
CFG.feature_cols = [i for i in df_train.columns.to_list() if i not in ['pressure','id', 'breath_id']]
print(len(CFG.feature_cols ))

98
95


## Utils

In [12]:
# LINEに通知
import requests
def send_line_notification(message):
    env = ""
    if IN_COLAB: env = "colab"
    elif IN_KAGGLE: env = "kaggle"
    elif LOCAL: env = "local"
        
    line_token = '8vBbxd0jENU39kV2ROEwp78jAzeankBFi7AG0JjoU3j'
    endpoint = 'https://notify-api.line.me/api/notify'
    message = f"[{env}]{message}"
    payload = {'message': message}
    headers = {'Authorization': 'Bearer {}'.format(line_token)}
    requests.post(endpoint, data=payload, headers=headers)

## CV Split

In [13]:
# df_train["fold"] = -1
# Fold = GroupKFold(n_splits=CFG.n_fold)
# for n, (train_index, val_index) in enumerate(Fold.split(df_train, df_train[CFG.target_col], groups=df_train.breath_id.values)):
#      df_train.loc[val_index, 'fold'] = int(n)
# df_train['fold'] = df_train['fold'].astype(int)
# df_oof = df_train[["id","breath_id","u_out", "pressure", "fold"]].copy()
# print(df_train.groupby(['fold', 'breath_id']).size())

In [14]:
# 外からフォールドを取り込む
df_fold = pd.read_csv(INPUT_DIR / 'R_C_StratifiedKFold_15_821.csv')
#df_train = df_train.drop('fold', axis=1).merge(df_fold[["breath_id", "fold"]], on="breath_id", how='left')
df_train = df_train.merge(df_fold[["breath_id", "fold"]], on="breath_id", how='left')
df_oof = df_train[["id","breath_id","u_out", "pressure", "fold"]].copy()
print(df_train.groupby(['fold', 'breath_id']).size())
del df_fold

fold  breath_id
0     20           80
      52           80
      92           80
      94           80
      157          80
                   ..
14    125602       80
      125614       80
      125666       80
      125687       80
      125708       80
Length: 75450, dtype: int64


## Transforms

## Dataset

In [15]:
"""
X[0]でbreath_id1つ分のシーケンス長80のデータを取得できる
"""
class TrainDataset(Dataset):
    def __init__(self, X, y, u_out):
        self.X = X
        self.y = y
        self.u_out = u_out
        
    def __len__(self):
        return len(self.X)
    
    def __getitem__(self, idx):
        x = torch.FloatTensor(self.X[idx])
        u_out = torch.LongTensor(self.u_out[idx])
        label = torch.FloatTensor(self.y[idx]).squeeze(1)
        return x, u_out, label
    
class TestDataset(Dataset):
    def __init__(self, X, u_out):
        self.X = X
        self.u_out = u_out
        
    def __len__(self):
        return len(self.X)
    
    def __getitem__(self, idx):
        x = torch.FloatTensor(self.X[idx])
        u_out = torch.LongTensor(self.u_out[idx])
        return x, u_out

## Rankgauss & Reshape
pandas.DataFrameからnumpyに変換、シーケンス分をまとめる

In [16]:
# display(df_train[CFG.cate_cols].head())
# display(df_train[CFG.cont_cols].head())

In [17]:
# ランクガウス
# u_out=0のu_inだけランクガウス掛ける
QT = QuantileTransformer(random_state=0,output_distribution='normal',subsample=1000000)
QT.fit(df[df['u_out']==0]['u_in'].values.reshape(-1,1))

df_train['q_u_in'] = QT.transform(train['u_in'].values.reshape(-1,1))
df_test['q_u_in'] = QT.transform(test['u_in'].values.reshape(-1,1))

df_train.loc[df_train['u_out']==0,'u_in'] = df_train['q_u_in']
df_test.loc[df_test['u_out']==0,'u_in'] = df_test['q_u_in']
del df_train['q_u_in'], df_test['q_u_in'], df
gc.collect()

60

In [18]:
for col in tqdm(CFG.feature_cols):
    rs = RobustScaler(quantile_range=(20.0, 80.0))
    rs.fit(df_train[df_train['u_out']==0][[col]])
    #df_train[[col]] = rs.fit_transform(df_train[[col]])
    df_train[[col]] = rs.transform(df_train[[col]])
    df_test[[col]] = rs.transform(df_test[[col]])
display(df_train.head())
display(df_test.head())
df_train.describe().T.to_csv(OUTPUT_DIR + '/' + "describe.csv")

  0%|          | 0/95 [00:00<?, ?it/s]

id  breath_id  time_step      u_in  u_out  pressure  sum_per_breath  \
0  80          1   3.678750  2.963283    1.0 -6.470211        0.692973   
1  79          1   3.622077  2.961858    1.0 -6.540513        0.692973   
2  78          1   3.565484  2.960172    1.0 -6.329607        0.692973   
3  77          1   3.508811  2.958171    1.0 -6.610815        0.692973   
4  76          1   3.451905  2.955788    1.0 -6.399909        0.692973   

   uid_count        f1        f2  ...  shifted_u_in_cumsum  \
0   8.279597 -0.092160 -0.069668  ...            -0.683291   
1   8.279597 -0.092283 -0.069908  ...            -0.649535   
2   8.279597 -0.092429 -0.070182  ...            -0.608203   
3   8.279597 -0.092601 -0.070501  ...            -0.566320   
4   8.279597 -0.092805 -0.070875  ...            -0.519761   

   shifted_area_cumsum  shifted_u_in_shift_1_past  shifted_u_in_shift_2_past  \
0            -0.570726                  -3.278284                  -2.775307   
1            -0.570053                  -3.220239                  -2.775307   
2            -0.568549                   9.525937                  -2.725619   
3            -0.566199                  12.399958                   8.185695   
4            -0.562905                  12.608598                  10.645989   

   shifted_u_in_shift_1_future  shifted_u_in_shift_2_future  \
0                    10.906756                    13.194671   
1                    14.208089                    13.417237   
2                    14.447749                    15.309712   
3                    16.485584                    16.724421   
4                    18.008956                    16.626061   

   shifted_u_out_shift_1_past  shifted_u_out_shift_2_past  \
0                        -1.0                        -1.0   
1                        -1.0                        -1.0   
2                        -1.0                        -1.0   
3                        -1.0                        -1.0   
4                        -1.0                        -1.0   

   shifted_u_out_shift_1_future  fold  
0                          -1.0    12  
1                          -1.0    12  
2                          -1.0    12  
3                          -1.0    12  
4                          -1.0    12  

[5 rows x 99 columns]

id  breath_id  time_step      u_in  u_out  sum_per_breath  uid_count  \
0  80          0   3.395682  2.955134    1.0        0.572011   8.306045   
1  79          0   3.342502  2.952395    1.0        0.572011   8.306045   
2  78          0   3.289332  2.949181    1.0        0.572011   8.306045   
3  77          0   3.236135  2.945410    1.0        0.572011   8.306045   
4  76          0   3.182955  2.940987    1.0        0.572011   8.306045   

         f1        f2        f3  ...  shifted_area  shifted_u_in_cumsum  \
0 -0.092572 -0.069839 -0.114017  ...     -0.699228            -0.683444   
1 -0.092763 -0.070101 -0.114088  ...     -0.685280            -0.669644   
2 -0.092987 -0.070406 -0.114171  ...     -0.658069            -0.642740   
3 -0.093250 -0.070764 -0.114268  ...     -0.618640            -0.603756   
4 -0.093559 -0.071183 -0.114386  ...     -0.569805            -0.555425   

   shifted_area_cumsum  shifted_u_in_shift_1_past  shifted_u_in_shift_2_past  \
0            -0.570726                  -3.278284                  -2.775307   
1            -0.570465                  -3.278284                  -2.775307   
2            -0.569695                   1.956122                  -2.775307   
3            -0.568186                   6.926953                   1.705585   
4            -0.565763                  11.509336                   5.960845   

   shifted_u_in_shift_1_future  shifted_u_in_shift_2_future  \
0                     2.211452                     7.356367   
1                     7.921351                    12.244604   
2                    13.185048                    16.026799   
3                    17.257749                    19.122179   
4                    20.590882                    21.395066   

   shifted_u_out_shift_1_past  shifted_u_out_shift_2_past  \
0                        -1.0                        -1.0   
1                        -1.0                        -1.0   
2                        -1.0                        -1.0   
3                        -1.0                        -1.0   
4                        -1.0                        -1.0   

   shifted_u_out_shift_1_future  
0                          -1.0  
1                          -1.0  
2                          -1.0  
3                          -1.0  
4                          -1.0  

[5 rows x 97 columns]

In [19]:
# for col in tqdm(CFG.cont_cols):
#     ss = StandardScaler()
#     df_train[[col]] = ss.fit_transform(df_train[[col]])
#     df_test[[col]] = ss.transform(df_test[[col]])
# display(df_train.head())
# display(df_test.head())
# df_train.describe().T.to_csv(OUTPUT_DIR + '/' + "describe_ss.csv")

In [20]:
X = np.float32(df_train[CFG.feature_cols]).reshape(-1, 80, len(CFG.feature_cols))
U_out = np.float32(df_train[["u_out"]]).reshape(-1, 80)
test_X = np.float32(df_test[CFG.feature_cols]).reshape(-1, 80, len(CFG.feature_cols))
test_U_out = np.float32(df_test[["u_out"]]).reshape(-1, 80)
y = np.float32(df_train["pressure"]).reshape(-1, 80, 1)
Fold = np.int16(df_train["fold"]).reshape(-1, 80, 1)
Fold = Fold.mean(axis=1).flatten()
print(X.shape, U_out.shape, y.shape, test_X.shape, Fold.shape)

(75450, 80, 95) (75450, 80) (75450, 80, 1) (50300, 80, 95) (75450,)


In [21]:
# X, u_out, y になっているか確認
ds = TrainDataset(X,y, U_out)
for i in range(3):
    print("="*50)
    print(ds[0][i])
del ds

tensor([[ 3.6788,  2.9633,  1.0000,  ..., -1.0000, -1.0000, -1.0000],
        [ 3.6221,  2.9619,  1.0000,  ..., -1.0000, -1.0000, -1.0000],
        [ 3.5655,  2.9602,  1.0000,  ..., -1.0000, -1.0000, -1.0000],
        ...,
        [-0.6896,  0.4906,  0.0000,  ...,  0.0000,  0.0000,  0.0000],
        [-0.7460,  0.4052,  0.0000,  ...,  0.0000,  0.0000,  0.0000],
        [-0.8020, -0.6162,  0.0000,  ...,  0.0000,  0.0000, -1.0000]])
tensor([1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
        1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
        1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0])
tensor([ -6.4702,  -6.5405,  -6.3296,  -6.6108,  -6.3999,  -6.4702,  -6.7514,
         -6.3999,  -6.5405,  -6.7514,  -6.3999,  -6.8217,  -6.8217,  -6.5405,
         -6.8217,  -6.9623,  -6.5405,  -6.8217,  -7.0326,  -6.1187,  -7.3138,
         -7.1029,  -6.9623,  -7.5247,  -7.7356,  -7.2435,  

## DataModule

In [22]:
class DataModule(pl.LightningDataModule):
    """
    numpy arrayで受け取る
    """
    def __init__(self, tr_X, tr_y, tr_u_out,
                 val_X, val_y, val_u_out,
                 test_X, test_u_out, cfg):
        super().__init__()
        self.train_data = tr_X
        self.train_label = tr_y
        self.train_u_out = tr_u_out
        self.valid_data = val_X
        self.valid_label = val_y
        self.valid_u_out = val_u_out
        self.test_data = test_X
        self.test_u_out = test_u_out
        self.cfg = cfg
        
    def setup(self, stage=None):
        self.train_dataset = TrainDataset(self.train_data, self.train_label, self.train_u_out)
        self.valid_dataset = TrainDataset(self.valid_data, self.valid_label, self.valid_u_out)
        self.test_dataset = TestDataset(self.test_data, self.test_u_out)
        
    # Trainer.fit() 時に呼び出される
    def train_dataloader(self):
        return DataLoader(self.train_dataset, **self.cfg.loader['train'])

    # Trainer.fit() 時に呼び出される
    def val_dataloader(self):
        return DataLoader(self.valid_dataset, **self.cfg.loader['valid'])

    def test_dataloader(self):
        return DataLoader(self.test_dataset, **self.cfg.loader['valid'])

In [23]:
# Data = DataModule(X[Fold==0],y[Fold==0],X[Fold==1],y[Fold==1],X[Fold==2], CFG)
# Data.setup()
# loader = Data.train_dataloader()
# tmp = loader.__iter__()
# print(tmp.next())
# del Data, loader, tmp

## Pytorch Lightning Module

In [24]:
# ====================================================
# criterion
# ====================================================
def compute_metric(df, preds):
    """
    Metric for the problem, as I understood it.
    """
    
    y = np.array(df['pressure'].values.tolist())
    w = 1 - np.array(df['u_out'].values.tolist())
    
    assert y.shape == preds.shape and w.shape == y.shape, (y.shape, preds.shape, w.shape)
    
    mae = w * np.abs(y - preds)
    mae = mae.sum() / w.sum()
    
    return mae

# ケロッピ先生
def mask_smooth_l1_loss(predict, truth, m, beta=0.1):
    loss = F.smooth_l1_loss(predict[m], truth[m], beta=beta)
    return loss

class VentilatorLoss(nn.Module):
    """
    Directly optimizes the competition metric
    """
    def __call__(self, preds, y, u_out):
        w = 1 - u_out
        mae = w * (y - preds).abs()
        mae = mae.sum(-1) / w.sum(-1)

        return mae

def get_criterion():
    if CFG.criterion_name == 'BCEWithLogitsLoss':
        # plだとto(device)いらない
        criterion = nn.BCEWithLogitsLoss(reduction="mean")
    if CFG.criterion_name == 'CrossEntropyLoss':
        criterion = nn.CrossEntropyLoss()
    if CFG.criterion_name == 'CustomLoss1':
        # [reference]https://www.kaggle.com/theoviel/deep-learning-starter-simple-lstm
        criterion = VentilatorLoss()
    else:
        raise NotImplementedError
    return criterion
# ====================================================
# optimizer
# ====================================================
def get_optimizer(model: nn.Module, config: dict):
    """
    input:
    model:model
    config:optimizer_nameやlrが入ったものを渡す
    
    output:optimizer
    """
    optimizer_name = config.optimizer_name
    if 'Adam' == optimizer_name:
        return Adam(model.parameters(),
                    lr=config.lr,
                    weight_decay=config.weight_decay,
                    amsgrad=config.amsgrad)
    elif 'RAdam' == optimizer_name:
        return optim.RAdam(model.parameters(),
                           lr=config.lr,
                           weight_decay=config.weight_decay)
    elif 'AdamW' == optimizer_name:
        return torch.optim.AdamW(model.parameters(),
                                 lr=config.lr,
                                 weight_decay=config.weight_decay)
    elif 'Ranger' == optimizer_name:
        return optim.Ranger(model.parameters(),
                            lr=config.lr)
    elif 'sgd' == optimizer_name:
        return SGD(model.parameters(),
                   lr=config.lr,
                   momentum=0.9,
                   nesterov=True,
                   weight_decay=config.weight_decay,)
    else:
        raise NotImplementedError

# ====================================================
# scheduler
# ====================================================
def get_scheduler(optimizer):
    if CFG.scheduler=='ReduceLROnPlateau':
        """
        factor : 学習率の減衰率
        patience : 何ステップ向上しなければ減衰するかの値
        eps : nanとかInf回避用の微小数
        """
        scheduler = ReduceLROnPlateau(optimizer, mode='min', factor=CFG.factor, patience=CFG.patience, verbose=True, eps=CFG.eps, min_lr=CFG.min_lr)
    elif CFG.scheduler=='CosineAnnealingLR':
        """
        T_max : 1 半周期のステップサイズ
        eta_min : 最小学習率(極小値)
        """
        scheduler = CosineAnnealingLR(optimizer, T_max=CFG.T_max, eta_min=CFG.min_lr, last_epoch=-1)
    elif CFG.scheduler=='CosineAnnealingWarmRestarts':
        """
        T_0 : 初期の繰りかえし回数
        T_mult : サイクルのスケール倍率
        """
        scheduler = CosineAnnealingWarmRestarts(optimizer, T_0=CFG.T_0, T_mult=1, eta_min=CFG.min_lr, last_epoch=-1)
    else:
        raise NotImplementedError
    return scheduler

In [25]:
# ====================================================
# model
# ====================================================
#https://www.kaggle.com/l0glikelihood/0-1093-single-public-lb
class CustomModel(nn.Module):
    def __init__(self, cfg):
        insize = len(cfg.feature_cols)
        hidden = [1024, 512, 256, 128]
        super().__init__()
        self.cfg = cfg
        self.lstm1 = nn.LSTM(insize, hidden[0], batch_first=True, bidirectional=True)
        self.lstm2 = nn.LSTM(2 * hidden[0] + insize, hidden[1], batch_first=True, bidirectional=True)
        self.lstm3 = nn.LSTM(2 * (hidden[0]+ hidden[1]), hidden[2], batch_first=True, bidirectional=True)
        self.lstm4 = nn.LSTM(2 * (hidden[1]+ hidden[2]), hidden[3], batch_first=True, bidirectional=True)        
        self.head = nn.Sequential(
            nn.Linear(2 * (hidden[2]+ hidden[3]), hidden[3]),
            nn.SELU(),
        )
        
        self.pressure_in  = nn.Linear(hidden[3], 1)
        self.pressure_out = nn.Linear(hidden[3], 1) # dualのとき使う

        #----
        #initialisation : https://www.kaggle.com/junkoda/pytorch-lstm-with-tensorflow-like-initialization/notebook
        for name, p in self.named_parameters():
            if 'lstm' in name:
                if 'weight_ih' in name:
                    nn.init.xavier_uniform_(p.data)
                elif 'weight_hh' in name:
                    nn.init.orthogonal_(p.data)
                elif 'bias_ih' in name:
                    p.data.fill_(0)
                    # Set forget-gate bias to 1
                    n = p.size(0)
                    p.data[(n // 4):(n // 2)].fill_(1)
                elif 'bias_hh' in name:
                    p.data.fill_(0)

        for name, m in self.named_modules():
            if isinstance(m, nn.Linear):
                #print(name,m)
                nn.init.xavier_uniform_(m.weight.data)
                m.bias.data.fill_(0)

    def forward(self, x):
        #x = torch.cat((features3, z2, z3),axis = 2)
        bs = x.size(0)
        
        x1, _ = self.lstm1(x)
        concat1 = torch.cat((x, x1),axis = 2)
        
        x2, _ = self.lstm2(concat1)
        concat2 = torch.cat((x1, x2),axis = 2)
        
        x3, _ = self.lstm3(concat2)
        concat3 = torch.cat((x2, x3),axis = 2)

        x4, _ = self.lstm4(concat3)
        concat4 = torch.cat((x3, x4),axis = 2)

        x = self.head(concat4)
        pressure_in  = self.pressure_in(x).reshape(bs,80)
        # pressure_out = self.pressure_out(x).reshape(bs,80)
        return pressure_in
    
def get_model(cfg):
    model = CustomModel(cfg)
    return model

In [26]:
# modelの動作確認
model = get_model(CFG)
dataloader = DataLoader(TrainDataset(X[:100],  y[:100], U_out[:100]), 
                        batch_size=10,num_workers=0,shuffle=True)
tmp = dataloader.__iter__()
_x, _u_out, _label = tmp.next()

#print(_x.shape, _u_out.shape, _label.shape)
pressure = model(_x)
print(pressure.shape)
del model, dataloader, tmp, _x, _u_out, _label

torch.Size([10, 80])


In [27]:
# #schedulerの確認
# model = get_model(CFG)
# optimizer = get_optimizer(model, CFG)
# scheduler = get_scheduler(optimizer)
# from pylab import rcParams
# lrs = []
# for epoch in range(1, CFG.epochs+1):
#     scheduler.step(epoch-1)
#     lrs.append(optimizer.param_groups[0]["lr"])
# rcParams['figure.figsize'] = 20,3
# print(lrs)
# plt.plot(lrs)

In [28]:
class Trainer(pl.LightningModule):
    def __init__(self, cfg):
        super().__init__()
        self.cfg = cfg
        self.model = get_model(cfg)
        self.criterion = get_criterion()
    
    def forward(self, x):
        output = self.model(x)
        return output
    
    def training_step(self, batch, batch_idx):
        x, u_out, y = batch
        pressure_in = self.forward(x)
        labels = y#.unsqueeze(1)
        
        score = self.criterion(pressure_in, labels ,u_out).mean().item() # mae
        loss = mask_smooth_l1_loss(pressure_in, labels, u_out<0.5) # u_out=0 のl1smooth
        #loss2 = mask_smooth_l1_loss(pressure_out, labels, u_out>0.5) # u_out=1のl1smooth
        #loss = 0.5* loss1 + 0.5*loss2
        
        #self.log_dict(dict(train_loss=loss))
        self.log('train_loss', loss, on_step=True, prog_bar=True, logger=True)
        # ここのlossはitemつけちゃだめ
        return {"loss": loss, "predictions": pressure_in, "labels": labels, "score":score}
    
    def training_epoch_end(self, outputs):
        loss = 0
        for output in outputs:
            loss += output['loss']
        loss = loss/len(outputs)
        self.log('train_loss_epoch', loss, logger=True)
        self.log("lr", self.optimizer.param_groups[0]['lr'], prog_bar=True, logger=True)
    
    def validation_step(self, batch, batch_idx):
        x, u_out, y = batch
        pressure_in = self.forward(x)
        labels = y#.unsqueeze(1)
        
        score = self.criterion(pressure_in, labels ,u_out).mean().item()
        loss = mask_smooth_l1_loss(pressure_in, labels, u_out<0.5)
        #loss2 = mask_smooth_l1_loss(pressure_out, labels, u_out>0.5)
        #loss = 0.5*loss1 + 0.5*loss2
        self.log('val_loss', loss, on_step= True, prog_bar=True, logger=True)
        return {"predictions": pressure_in,
                "labels": labels,
                "loss": loss.item(),
                "score": score}
    
    def validation_epoch_end(self, outputs):
        preds = []
        labels = []
        loss = 0
        score = 0
        for output in outputs:
            preds += output['predictions']
            labels += output['labels']
            loss += output['loss']
            score += output['score']

        labels = torch.stack(labels)
        preds = torch.stack(preds)
        loss = loss/len(outputs)
        score = score/len(outputs)
        
        self.log("val_loss_epoch", loss, prog_bar=True, logger=True)
        self.log("val_mae_epoch", score,logger=True)
        
    def predict_step(self, batch, batch_idx):
        
        x, u_out = batch
        pressure = self.forward(x)
        #pressure = pressure_in*(1-u_out) + pressure_out*u_out
        return pressure
        
    def test_step(self, batch, batch_idx):
        x, u_out = batch       
        output = self.forward(x)
        return output
    
    def configure_optimizers(self):
        self.optimizer = get_optimizer(self, self.cfg)
        self.scheduler = {'scheduler': get_scheduler(self.optimizer),
                          "monitor": "val_loss_epoch",
                          'interval': 'epoch', # 'step'or 'epoch'
#                           'interval': 'step', # 'step'or 'epoch'
                          'frequency': 1}
        return {'optimizer': self.optimizer, 'lr_scheduler': self.scheduler}

## Train

In [29]:
def train() -> None:
    for fold in range(CFG.n_fold):
        if not fold in CFG.trn_fold:
            continue
        print(f"{'='*38} Fold: {fold} {'='*38}")
        # Logger
        #======================================================
        lr_monitor = LearningRateMonitor(logging_interval='step')
        # 学習済重みを保存するために必要
        loss_checkpoint = ModelCheckpoint(
            dirpath=OUTPUT_DIR,
            filename=f"best_loss_fold{fold}",
            monitor="val_loss_epoch",
            save_last=True,
            save_top_k=1,
            save_weights_only=True,
            mode="min",
        )
        csv_logger = CSVLogger(save_dir=str(OUTPUT_DIR), name=f"fold_{fold}")
        wandb_logger = WandbLogger(
            project=f'{CFG.competition}',
            group= f'{CFG.exp_name}',
            name = f'Fold{fold}',
            save_dir=OUTPUT_DIR
        )
        data_module = DataModule(X[Fold!=fold], y[Fold!=fold],U_out[Fold!=fold],
                                 X[Fold==fold], y[Fold==fold],U_out[Fold==fold],
                                 test_X, test_U_out,
                                 CFG
                                )
        data_module.setup()
        
        CFG.T_max = int(math.ceil(len(data_module.train_dataloader())/CFG.grad_acc)*CFG.epochs)
        print(f"set schedular T_max {CFG.T_max}")
        early_stopping_callback = EarlyStopping(monitor='val_loss_epoch', mode="min", patience=30)
        
        trainer = pl.Trainer(
            logger=[csv_logger,wandb_logger],
            callbacks=[loss_checkpoint, early_stopping_callback],#lr_monitor,early_stopping_callback
            default_root_dir=OUTPUT_DIR,
            accumulate_grad_batches=CFG.grad_acc,
            max_epochs=CFG.epochs,
            precision=CFG.precision,
            **CFG.trainer
        )
        # 学習
        model = Trainer(CFG)
        trainer.fit(model, data_module)
        torch.save(model.model.state_dict(),OUTPUT_DIR + '/' + f'{CFG.exp_name}_fold{fold}.pth')
        
        del model, data_module
        # テストデータを予測して保存
        if CFG.inference:
            data_module = DataModule(X[0:1], y[0:1], U_out[0:1],
                                     X[0:1], y[0:1], U_out[0:1], 
                                     test_X, test_U_out, CFG)
            data_module.setup()
            # best loss modelのロード
            best_model = Trainer.load_from_checkpoint(cfg=CFG,checkpoint_path=loss_checkpoint.best_model_path)
            predictions = trainer.predict(best_model, data_module.test_dataloader())
            preds = []
            for p in predictions:
                preds += p
            preds = torch.stack(preds).flatten()
            submission['pressure'] = preds.to('cpu').detach().numpy()
            submission.to_csv(OUTPUT_DIR + '/' + f'submission_fold{fold}.csv',index=False)
            
            # oof
            data_module = DataModule(X[0:1], y[0:1], U_out[0:1],
                                     X[0:1], y[0:1], U_out[0:1],
                                     X[Fold==fold], U_out[Fold==fold], CFG)
            data_module.setup()
            predictions = trainer.predict(best_model, data_module.test_dataloader())
            preds = []
            for p in predictions:
                preds += p
            preds = torch.stack(preds).flatten()
            df_oof.loc[df_oof["fold"] == fold, ['pred']] = preds.to('cpu').detach().numpy()
            df_oof.to_csv(OUTPUT_DIR + '/' + f'oof.csv',index=False)
        
        wandb.finish()

        

In [30]:
train()
send_line_notification("finished")
wandb.finish()


====================================== Fold: 0 ======================================


Using native 16bit precision.
GPU available: True, used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs


set schedular T_max 140288


D:\python\Anaconda3\lib\site-packages\pytorch_lightning\core\datamodule.py:424: LightningDeprecationWarning: DataModule.setup has already been called, so it will not be called again. In v1.6 this behavior will change to always call DataModule.setup.
  f"DataModule.{name} has already been called, so it will not be called again. "
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
wandb: wandb version 0.12.7 is available!  To upgrade, please run:
wandb:  $ pip install wandb --upgrade



  | Name      | Type           | Params
---------------------------------------------
0 | model     | CustomModel    | 28.7 M
1 | criterion | VentilatorLoss | 0     
---------------------------------------------
28.7 M    Trainable params
0         Non-trainable params
28.7 M    Total params
114.763   Total estimated model params size (MB)


...

D:\python\Anaconda3\lib\site-packages\pytorch_lightning\trainer\deprecated_api.py:33: LightningDeprecationWarning: `Trainer.train_loop` has been renamed to `Trainer.fit_loop` and will be removed in v1.6.
  "`Trainer.train_loop` has been renamed to `Trainer.fit_loop` and will be removed in v1.6."
D:\python\Anaconda3\lib\site-packages\pytorch_lightning\core\datamodule.py:424: LightningDeprecationWarning: DataModule.prepare_data has already been called, so it will not be called again. In v1.6 this behavior will change to always call DataModule.prepare_data.
  f"DataModule.{name} has already been called, so it will not be called again. "
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Predicting: 137it [00:00, ?it/s]

LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Predicting: 137it [00:00, ?it/s]

D:\python\Anaconda3\lib\site-packages\pytorch_lightning\core\datamodule.py:424: LightningDeprecationWarning: DataModule.teardown has already been called, so it will not be called again. In v1.6 this behavior will change to always call DataModule.teardown.
  f"DataModule.{name} has already been called, so it will not be called again. "


In [31]:
oof = pd.read_csv(OUTPUT_DIR + 'oof.csv')
oof = oof.dropna(subset=['pred'])
cv = compute_metric(oof,oof["pred"])
print(f"cv:{cv}")

cv:0.12704652543416375


In [32]:
# # median
submission = pd.read_csv(INPUT_DIR / "sample_submission.csv")
n_fold = 15
preds = [pd.read_csv(f'F:/Kaggle/ventilator-pressure-prediction/data/output/{CFG.exp_name}/submission_fold{i}.csv') for i in range(n_fold)]
#print(preds[0].pressure[0],preds[1].pressure[0],preds[2].pressure[0],preds[3].pressure[0],preds[4].pressure[0])
submission['pressure'] = np.median([i.pressure for i in preds],axis=0)

# reverseしてるので戻す
submission["id"] = df_test["id"]
submission = submission.sort_values("id").reset_index(drop=True)

submission.to_csv(f'F:/Kaggle/ventilator-pressure-prediction/data/output/{CFG.exp_name}/{CFG.exp_name}_{n_fold}fold_median.csv',index=False)
submission.head()

id  pressure
0   1     6.273
1   2     6.000
2   3     7.200
3   4     7.700
4   5     9.160

In [33]:
# sub = pd.read_csv(f'F:/Kaggle/ventilator-pressure-prediction/data/output/{CFG.exp_name}/submission_fold0.csv')
# sub["id"] = df_test["id"]
# sub = sub.sort_values("id").reset_index(drop=True)
# sub.to_csv(f'F:/Kaggle/ventilator-pressure-prediction/data/output/{CFG.exp_name}/{CFG.exp_name}_並び順正規化.csv',index=False)

In [34]:
# fold_num = 0
# data_module = DataModule(X[0:1], y[0:1], U_out[0:1],X[0:1], y[0:1], U_out[0:1], test_X, test_U_out, CFG)
# data_module.setup()
# # best loss modelのロード
# checkpoint_path = f"F:/Kaggle/ventilator-pressure-prediction/data/output/{CFG.exp_name}/best_loss_fold{fold_num}.ckpt"
# best_model = Trainer.load_from_checkpoint(cfg=CFG, checkpoint_path=checkpoint_path)
# trainer = pl.Trainer(
#             default_root_dir=OUTPUT_DIR,
#             accumulate_grad_batches=CFG.grad_acc,
#             max_epochs=CFG.epochs,
#             precision=CFG.precision,
#             **CFG.trainer
#         )
# predictions = trainer.predict(best_model, data_module.test_dataloader())
# preds = []
# for p in predictions:
#     preds += p
# preds = torch.stack(preds).flatten()
# submission['pressure'] = preds.to('cpu').detach().numpy()
# print(submission.isnull().sum())
# submission.to_csv(OUTPUT_DIR + '/' + f'submission_fold{fold_num}.csv',index=False)

In [35]:
oof.sort_values("id").reset_index(drop=True).to_csv(OUTPUT_DIR + '/' + f'oof.csv',index=False)